In [2]:
import matplotlib.pyplot as plt

In [ ]:
# -*- coding: utf-8 -*-
"""
Created on Sun May  2 19:50:14 2021

@author: VanGV
"""
import dash
import dash_core_components as dcc
import dash_html_components as html
import webbrowser
import dash
from dash.dependencies import Input, Output, State
import dash_table
import dash_core_components as dcc
import dash_html_components as html
import sqlite3
import pandas as pd
import numpy as np
import dash_core_components as dcc
import plotly.express as px
import matplotlib.pyplot as plt
import os
import wfdb
from scipy import signal
import dash
import dash_auth
import dash_core_components as dcc
import dash_html_components as html
import plotly
# Since we're adding callbacks to elements that don't exist in the app.layout,
# Dash will raise an exception to warn us that we might be
# doing something wrong.
# In this case, we're adding the elements through a callback, so we can ignore
# the exception.

cnx = sqlite3.connect('data/databases/patients.db')
df = pd.read_sql_query("SELECT * FROM patients", cnx)

params_df_page_2 = [
    'Дата обследования', 'ЭКГ', 'Температура', 'Пульс'
]

external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']

# Keep this out of source code repository - save in a file or a database
VALID_USERNAME_PASSWORD_PAIRS = {
    '0000': '0000'
}

app = dash.Dash(__name__, suppress_callback_exceptions=True, external_stylesheets=external_stylesheets)
auth = dash_auth.BasicAuth(
    app,
    VALID_USERNAME_PASSWORD_PAIRS
)

app.layout = html.Div([
    dcc.Location(id='url', refresh=False),
    html.Div(id='page-content'),
    dcc.Store(id='active_cell_value'),
    dcc.Store(id='database'),
])


index_page = html.Div([
    dcc.Link('Запустить приложение', href='/page-1'),
    #html.Br(),
    #dcc.Link('Go to Page 2', href='/page-2'),
])

page_1_layout = html.Div([
    
    html.Br(),
    html.Div(id='page-1-content'),
    html.Br(),
    
    
    
    dash_table.DataTable(
        id='adding-rows-table',
        data=df.to_dict('records'),
        columns=[{'id': c, 'name': c} for c in df.columns],

        filter_action="native",
        sort_action="native",
        sort_mode="multi",
        column_selectable="single",
        row_selectable="multi",
        selected_columns=[],
        selected_rows=[],
        page_action="native",
        page_current= 0,
        page_size= 10,
        
        editable=True,
        row_deletable=True
    ),

    html.Button('Добавить пациента', id='editing-rows-button', n_clicks=0),
    html.Button('Обновить базу данных', id='update-bd-button', n_clicks=0),
])


page_2_layout = html.Div([
    html.Div(id='page-content_2'),
    html.Br(),
    dcc.Upload(
        id='upload-data',
        children=html.Div([
            'Загрузить ',
            html.A('запись')
        ]),
        style={
            'width': '100%',
            'height': '60px',
            'lineHeight': '60px',
            'borderWidth': '1px',
            'borderStyle': 'dashed',
            'borderRadius': '5px',
            'textAlign': 'center',
            'margin': '10px'
        },
        # Allow multiple files to be uploaded
        multiple=True
    ),
    html.Br(),
    html.Div(id='output-data-upload'),
    dash_table.DataTable(
        id='df_page_2',
        
        columns=[{'id': c, 'name': c} for c in params_df_page_2],

        filter_action="native",
        sort_action="native",
        sort_mode="multi",
        column_selectable="single",
        row_selectable="multi",
        selected_columns=[],
        selected_rows=[],
        page_action="native",
        page_current= 0,
        page_size= 10,
        
        editable=True,
        row_deletable=True
    ),
    html.Br(),
    html.Div([
    dcc.Graph(id = 'ecg_graph'),
    html.Br(),
    dcc.Graph(id = 'pulse_graph'),
    html.Br(),
    dcc.Graph(id = 't_graph'),
    html.Br()],
        
    style={'width': '70%',
          'display': 'inline-block'}
    ),
    
    html.Div([
    html.P(id = 'ecg_f'),
    html.Br(),
    html.P('1', id = 'pulse_f'),
    html.Br(),
    html.P('2',id = 't_f'),
    html.Br()],
        
    style={'width': '20%',
          'display': 'inline-block',
          'position': 'relative'}
    )
    
])


@app.callback(
    Output('adding-rows-table', 'data'),
    Input('editing-rows-button', 'n_clicks'),
    State('adding-rows-table', 'data'),
    State('adding-rows-table', 'columns'))
def add_row(n_clicks, rows, columns):
    if n_clicks > 0:
        temp_dict = {c['id']: '' for c in columns}
        print(type(temp_dict))
        print(type(temp_dict))
        rows.append(temp_dict)
    return rows

@app.callback(
    Output('url', 'pathname'),
    Output('active_cell_value', 'value'),
    Input('adding-rows-table', 'active_cell'))
def display_page(active_cell):
    #print(active_cell)
    if active_cell['column_id'] == 'ID':
        active_row_id = active_cell['row'] if active_cell else None
        print(active_row_id)
        print('active_cell', active_cell)
        return '/page-2', active_row_id
    else: None

@app.callback(
    Output('df_page_2', 'data'),
    Input('active_cell_value', 'value'))
def plot_t(value):
    active_row_id = value
    print(value)
    print(active_row_id)
    
    if active_row_id != None:
        try:
            data_folder = 'data/signals'
            all_patients = os.listdir(data_folder)
            patients_id = [i.split('_')[-1] for i in all_patients]
            all_dates_folder = os.listdir(data_folder + '/' + 'patients_' + patients_id[active_row_id])
            data=[
                dict({'Дата обследования': all_dates_folder[i], 
                      'ЭКГ':len(os.listdir(data_folder + '/' + 'patients_' + patients_id[active_row_id] + '/' + all_dates_folder[i] + '/ecg')) > 0, 
                      'Температура':len(os.listdir(data_folder + '/' + 'patients_' + patients_id[active_row_id] + '/' + all_dates_folder[i] + '/temperature')) > 0, 
                      'Пульс':len(os.listdir(data_folder + '/' + 'patients_' + patients_id[active_row_id] + '/' + all_dates_folder[i] + '/pulse')) > 0})
                for i in range(len(all_dates_folder))
            ]
        except:
            data = [dict({'Дата обследования': 'None',
                          'ЭКГ':'None',
                          'Температура':'None',
                          'Пульс':'None'})
            ]
    else: 
        data = [dict({'Дата обследования': 'None',
                      'ЭКГ':'None',
                      'Температура':'None',
                      'Пульс':'None'})
        ]
        
    return data        
        
#@app.callback(
#    Output(),
#    Input('adding-rows-table', 'data'),
#    Input('editing-rows-button', 'n_clicks'))
#def save_bd(n_clicks):
#    if n_clicks > 0:
#        df = pd.read_sql_query("SELECT * FROM patients", cnx)
#        df = df.append(pd.DataFrame([[1,2,3,4,5,6,7,8,9]], columns = df.columns))
#        df.to_sql('patients', cnx, if_exists='replace', index=False)
#        cnx.commit()
#        cnx.close()
#        
#        cnx = sqlite3.connect('patients.db')
#        df = pd.read_sql_query("SELECT * FROM patients", cnx)

@app.callback(
    Output('t_graph', 'figure'),
    Output('t_f', 'children'),
    Input('active_cell_value', 'value'),
    Input('df_page_2', 'active_cell'),
    Input('df_page_2', 'data'))
def plot_t(value, active_cell, data):
    active_row_id = value
    active_cell = active_cell['row'] if active_cell else None
    #print(value)
    #print(active_row_id)
    
    if active_row_id != None:
    
        data_folder = 'data/signals'
        all_patients = os.listdir(data_folder)
        patients_id = [i.split('_')[-1] for i in all_patients]
        patient_rec = os.listdir(data_folder + '/' + 'patients_' + patients_id[active_row_id] + '/' + data[active_cell]['Дата обследования'] + '/temperature')
        all_data = pd.read_csv(data_folder + '/' + 'patients_' + patients_id[active_row_id]+ '/' + data[active_cell]['Дата обследования'] + '/temperature/' + patient_rec[0], skiprows = 9, sep = ';')
        
        data_t = all_data[all_data.columns[0]]
        #b, a = signal.butter(2, 0.05, btype='high', fs = 250)
        #data = signal.filtfilt(b, a, data)
        #b, a = signal.iirnotch(50, 30, fs=250)
        #data = signal.filtfilt(b, a, data)
        #print(data)
        fig = px.line(data_t)
    else:
        fig = px.line(np.array([0,0,0,0,0,0,0,0,0,0]))
    fig.update_xaxes(title_text='Температура', range=(0, 500))
    fig.update_yaxes(title_text='С')
    return fig, 'Средняя температура "{}"'.format(np.mean(data_t))

@app.callback(
    Output('pulse_graph', 'figure'),
    Output('pulse_f', 'children'),
    Input('active_cell_value', 'value'),
    Input('df_page_2', 'active_cell'),
    Input('df_page_2', 'data'))
def plot_ecg(value, active_cell, data):
    active_row_id = value
    active_cell = active_cell['row'] if active_cell else None
    #print(value)
    #print(active_row_id)
    
    if active_row_id != None:
        data_folder = 'data/signals'
        all_patients = os.listdir(data_folder)
        patients_id = [i.split('_')[-1] for i in all_patients]
        patient_rec = os.listdir(data_folder + '/' + 'patients_' + patients_id[active_row_id] + '/' + data[active_cell]['Дата обследования'] + '/pulse')
        record = wfdb.rdrecord(data_folder + '/' + 'patients_' + patients_id[active_row_id] + '/' + data[active_cell]['Дата обследования'] + '/pulse/' + patient_rec[1][:-4], sampto=7500) 
        fig = px.line(record.p_signal)
        
        #print(record.p_signal)
    else:
        fig = px.line(np.array([0,0,0,0,0,0,0,0,0,0]))
    fig.update_xaxes(title_text='Пульсовая волна', range=(0, 500))
    fig.update_yaxes(title_text='mmHg')   
    
    return fig, 'Средняя пульсовая волна "{}"'.format(np.mean(record.p_signal))


@app.callback(
    Output('ecg_graph', 'figure'),
    Input('active_cell_value', 'value'),
    Input('df_page_2', 'active_cell'),
    Input('df_page_2', 'data'))
def plot_ecg(value, active_cell, data):
    active_row_id = value
    active_cell = active_cell['row'] if active_cell else None
    #print(value)
    #print(active_row_id)
    
    if active_row_id != None:
        data_folder = 'data/signals'
        all_patients = os.listdir(data_folder)
        patients_id = [i.split('_')[-1] for i in all_patients]
        patient_rec = os.listdir(data_folder + '/' + 'patients_' + patients_id[active_row_id] + '/' + data[active_cell]['Дата обследования'] + '/ecg')
        record = wfdb.rdrecord(data_folder + '/' + 'patients_' + patients_id[active_row_id] + '/' + data[active_cell]['Дата обследования'] + '/ecg/' + patient_rec[1][:-4], sampto=2500) 
        fig = px.line(record.p_signal)
        
        #print(record.p_signal)
    else:
        fig = px.line(np.array([0,0,0,0,0,0,0,0,0,0]))
    fig.update_xaxes(title_text='Электрокардиограмма', range=(0, 500))
    fig.update_yaxes(title_text='mV')   
    
    return fig

# Update the index
@app.callback(
    Output('page-content', 'children'),
#    Output('', 'data'),
#    Output('','columns'),
    Input('url', 'pathname'))
def display_page(pathname):
    if pathname == '/page-1':
#        try: 
#            cnx.commit()
#            cnx.close()
#       except: 
#            None
            
#        cnx = sqlite3.connect('patients.db')
#        df = pd.read_sql_query("SELECT * FROM patients", cnx)
        
        return page_1_layout
    elif pathname == '/page-2':
        return page_2_layout
    else:
        return index_page
    # You could also return a 404 "URL not found" page here


if __name__ == '__main__':
    app.run_server(host='localhost', port='3030', debug=False)
    webbrowser.open('http://localhost:3030/', new=2)

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is running on http://localhost:3030/

Dash is run

 * Running on http://localhost:3030/ (Press CTRL+C to quit)
127.0.0.1 - - [11/May/2021 23:54:03] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [11/May/2021 23:54:04] "GET /_dash-layout HTTP/1.1" 200 -
127.0.0.1 - - [11/May/2021 23:54:05] "GET /_dash-dependencies HTTP/1.1" 200 -
127.0.0.1 - - [11/May/2021 23:54:05] "POST /_dash-update-component HTTP/1.1" 200 -
127.0.0.1 - - [11/May/2021 23:54:06] "POST /_dash-update-component HTTP/1.1" 200 -
127.0.0.1 - - [11/May/2021 23:54:06] "GET /_dash-component-suites/dash_table/async-highlight.js HTTP/1.1" 200 -
127.0.0.1 - - [11/May/2021 23:54:06] "GET /_dash-component-suites/dash_table/async-table.js HTTP/1.1" 200 -


Exception on /_dash-update-component [POST]
Traceback (most recent call last):
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 2447, in wsgi_app
    response = self.full_dispatch_request()
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1952, in full_dispatch_request
    rv = self.handle_user_exception(e)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1821, in handle_user_exception
    reraise(exc_type, exc_value, tb)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\_compat.py", line 39, in reraise
    raise value
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1950, in full_dispatch_request
    rv = self.dispatch_request()
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1936, in dispatch_request
    return self.view_functions[rule.endpoint](**req.view_args)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\dash_auth\basic_auth.py", line 33, in wrap
    response 

Exception on /_dash-update-component [POST]
Traceback (most recent call last):
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 2447, in wsgi_app
    response = self.full_dispatch_request()
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1952, in full_dispatch_request
    rv = self.handle_user_exception(e)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1821, in handle_user_exception
    reraise(exc_type, exc_value, tb)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\_compat.py", line 39, in reraise
    raise value
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1950, in full_dispatch_request
    rv = self.dispatch_request()
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1936, in dispatch_request
    return self.view_functions[rule.endpoint](**req.view_args)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\dash_auth\basic_auth.py", line 33, in wrap
    response 

Exception on /_dash-update-component [POST]
Traceback (most recent call last):
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 2447, in wsgi_app
    response = self.full_dispatch_request()
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1952, in full_dispatch_request
    rv = self.handle_user_exception(e)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1821, in handle_user_exception
    reraise(exc_type, exc_value, tb)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\_compat.py", line 39, in reraise
    raise value
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1950, in full_dispatch_request
    rv = self.dispatch_request()
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1936, in dispatch_request
    return self.view_functions[rule.endpoint](**req.view_args)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\dash_auth\basic_auth.py", line 33, in wrap
    response 

...

Exception on /_dash-update-component [POST]
Traceback (most recent call last):
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 2447, in wsgi_app
    response = self.full_dispatch_request()
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1952, in full_dispatch_request
    rv = self.handle_user_exception(e)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1821, in handle_user_exception
    reraise(exc_type, exc_value, tb)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\_compat.py", line 39, in reraise
    raise value
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1950, in full_dispatch_request
    rv = self.dispatch_request()
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1936, in dispatch_request
    return self.view_functions[rule.endpoint](**req.view_args)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\dash_auth\basic_auth.py", line 33, in wrap
    response 

Exception on /_dash-update-component [POST]
Traceback (most recent call last):
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 2447, in wsgi_app
    response = self.full_dispatch_request()
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1952, in full_dispatch_request
    rv = self.handle_user_exception(e)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1821, in handle_user_exception
    reraise(exc_type, exc_value, tb)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\_compat.py", line 39, in reraise
    raise value
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1950, in full_dispatch_request
    rv = self.dispatch_request()
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1936, in dispatch_request
    return self.view_functions[rule.endpoint](**req.view_args)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\dash_auth\basic_auth.py", line 33, in wrap
    response 

127.0.0.1 - - [12/May/2021 09:19:26] "POST /_dash-update-component HTTP/1.1" 500 -


Exception on /_dash-update-component [POST]
Traceback (most recent call last):
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 2447, in wsgi_app
    response = self.full_dispatch_request()
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1952, in full_dispatch_request
    rv = self.handle_user_exception(e)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1821, in handle_user_exception
    reraise(exc_type, exc_value, tb)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\_compat.py", line 39, in reraise
    raise value
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1950, in full_dispatch_request
    rv = self.dispatch_request()
  File "C:\Users\VanGV\anaconda3\lib\site-packages\flask\app.py", line 1936, in dispatch_request
    return self.view_functions[rule.endpoint](**req.view_args)
  File "C:\Users\VanGV\anaconda3\lib\site-packages\dash_auth\basic_auth.py", line 33, in wrap
    response 

127.0.0.1 - - [12/May/2021 09:19:26] "POST /_dash-update-component HTTP/1.1" 500 -
127.0.0.1 - - [12/May/2021 09:19:28] "POST /_dash-update-component HTTP/1.1" 200 -
127.0.0.1 - - [12/May/2021 09:19:29] "POST /_dash-update-component HTTP/1.1" 200 -
127.0.0.1 - - [12/May/2021 09:19:29] "POST /_dash-update-component HTTP/1.1" 200 -
127.0.0.1 - - [12/May/2021 13:11:15] "GET /page-2 HTTP/1.1" 403 -
127.0.0.1 - - [12/May/2021 13:11:19] "GET /page-2 HTTP/1.1" 403 -
127.0.0.1 - - [12/May/2021 13:11:21] "GET /page-2 HTTP/1.1" 403 -
